In [ ]:
# Other Releated Installation 

! pip install pysrt
! pip install Cython
! pip install ctc_segmentation==1.1.0
! pip install num2words
! apt-get update && apt-get install -y libsndfile1 ffmpeg
!apt-get install -y swig
!pip install torchaudio>=0.6.0 -f https://download.pytorch.org/whl/torch_stable.html
!mkdir configs

# BRANCH = 'r1.0.0rc1'
BRANCH = 'v1.0.0'
!python -m pip install git+https://github.com/NVIDIA/NeMo.git@$BRANCH#egg=nemo_toolkit[all]
!git clone https://github.com/NVIDIA/NeMo -b "$BRANCH"


!cd NeMo && bash scripts/asr_language_modeling/ngram_lm/install_beamsearch_decoders.sh


! pip install git+https://github.com/LIAAD/yake
! pip install phonetics
! pip install fuzzywuzzy
! pip install PyPDF2

In [2]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!wget -P configs/ https://raw.githubusercontent.com/NVIDIA/NeMo/main/examples/asr/conf/config.yaml

--2021-06-03 04:59:09--  https://raw.githubusercontent.com/NVIDIA/NeMo/main/examples/asr/conf/config.yaml
Resolving raw.githubusercontent.com (raw.githubusercontent.com)... 185.199.108.133, 185.199.109.133, 185.199.110.133, ...
Connecting to raw.githubusercontent.com (raw.githubusercontent.com)|185.199.108.133|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 4040 (3.9K) [text/plain]
Saving to: ‘configs/config.yaml’

config.yaml         100%[===================>]   3.95K  --.-KB/s    in 0s      

2021-06-03 04:59:09 (55.1 MB/s) - ‘configs/config.yaml’ saved [4040/4040]



# Setup 

In [ ]:
import pathlib as plib
import pysrt
import moviepy.editor as editor
import IPython
from pydub import AudioSegment, silence
import numpy as np
from plotly import graph_objects as go
from IPython.display import Audio, display
import librosa
import nemo.collections.asr as nemo_asr
import torch
from torch.utils.data import TensorDataset, DataLoader
import ctc_decoders

import IPython.display as ipd
import pandas as pd
import os
import yake
import soundfile as sf

# Import the data augmentation component from ASR collection
from nemo.collections.asr.parts import perturb, segment

import IPython.display as ipd
import numpy as np
from PIL import Image
from matplotlib.pyplot import imshow
from matplotlib import pyplot as plt
import phonetics
from fuzzywuzzy import fuzz

import wget
import re
import json
import scipy.io.wavfile as wav
import PyPDF2
import os, shutil

In [2]:
BRANCH = 'v1.0.0'
root_path = plib.Path("/content/drive/MyDrive/cs230_project")

pd.set_option('display.max_rows', 500)
pd.set_option('display.float_format', lambda x: '%.6f' % x)

# MIT Lecture Example 

In [3]:
## create data directory and download an audio file
WORK_DIR = str(root_path / 'MIT_usecase')
DATA_DIR = WORK_DIR + '/DATA'
os.makedirs(DATA_DIR, exist_ok=True)
audio_file = 'MIT_AI_12B.mp3'
OUTPUT_DIR = WORK_DIR + '/output'
WINDOW = 8000

high_score_manifest = str(WINDOW) + '_' + audio_file.replace('.mp3', '_high_score_manifest.json')

## Data Preparation 
The data preparation section obtains a series of audio segments from MIT lectures using the nemo ASR and CTC segmentation. We select the high confidence json file as our dataset. This only needs to be run once. All outputs are cleared from cell since they are not so relevant after the data preparation process

In [ ]:
# If you're running the notebook locally, update the TOOLS_DIR path below
# In Colab, a few required scripts will be downloaded from NeMo github
# this section many code is adopted from https://colab.research.google.com/github/NVIDIA/NeMo/blob/main/tutorials/tools/CTC_Segmentation_Tutorial.ipynb

TOOLS_DIR = './content/NeMo/tools/ctc_segmentation/scripts'

if 'google.colab' in str(get_ipython()):
    TOOLS_DIR = 'scripts/'
    os.makedirs(TOOLS_DIR, exist_ok=True)

    required_files = ['prepare_data.py',
                    'normalization_helpers.py',
                    'run_ctc_segmentation.py',
                    'verify_segments.py',
                    'cut_audio.py',
                    'process_manifests.py',
                    'utils.py']
    for file in required_files:
        if not os.path.exists(os.path.join(TOOLS_DIR, file)):
            file_path = 'https://raw.githubusercontent.com/NVIDIA/NeMo/' + BRANCH + '/tools/ctc_segmentation/' + TOOLS_DIR + file
            print(file_path)
            wget.download(file_path, TOOLS_DIR)
elif not os.path.exists(TOOLS_DIR):
      raise ValueError(f'update path to NeMo root directory')

In [4]:
## create data directory and download an audio file
WORK_DIR = str(root_path / 'MIT_usecase')
DATA_DIR = WORK_DIR + '/DATA'
os.makedirs(DATA_DIR, exist_ok=True)
audio_file = 'MIT_AI_12B.mp3'
OUTPUT_DIR = WORK_DIR + '/output'
WINDOW = 8000

In [ ]:
# load and write the transcript 
# Get the Transcript 
transcript_path = str(root_path / "MIT_usecase" /  "MIT_AI_12B.srt")
transcript = pysrt.open(transcript_path)

big_str = ''
for ele in transcript:
  big_str += ele.text + " "
big_str = re.sub('\[.*\]', '', big_str)
big_str = big_str.replace('PATRICK H. WINSTON', '').replace('AUDIENCE', '')

with open(os.path.join(DATA_DIR, audio_file.replace('mp3', 'txt')), 'w') as f:
    f.write(big_str)

In [ ]:
MODEL = 'QuartzNet15x5Base-En'

! python $TOOLS_DIR/prepare_data.py \
--in_text=$DATA_DIR \
--output_dir=$OUTPUT_DIR/processed/ \
--language='eng' \
--cut_prefix=3 \
--model=$MODEL \
--audio_dir=$DATA_DIR

In [ ]:
! python $TOOLS_DIR/run_ctc_segmentation.py \
--output_dir=$OUTPUT_DIR \
--data=$OUTPUT_DIR/processed \
--model=$MODEL \
--window_len=$WINDOW \
--no_parallel

In [ ]:
alignment_file = str(WINDOW) + '_' + audio_file.replace('.mp3', '_segments.txt')
! cat $OUTPUT_DIR/segments/$alignment_file

In [ ]:
OFFSET = 0
THRESHOLD = -5

! python $TOOLS_DIR/cut_audio.py \
--output_dir=$OUTPUT_DIR \
--model=$MODEL \
--alignment=$OUTPUT_DIR/segments/ \
--threshold=$THRESHOLD \
--offset=$OFFSET

In [ ]:
def display_samples(manifest):
    """ Display audio and reference text."""
    with open(manifest, 'r') as f:
        for line in f:
            sample = json.loads(line)
            sample_rate, signal = wav.read(sample['audio_filepath'])
            plot_signal(signal, sample_rate)
            display(Audio(sample['audio_filepath']))
            display('Reference text:       ' + sample['text_no_preprocessing'])
            display('ASR transcript: ' + sample['transcript'])
            print('\n' + '-' * 110)
def plot_signal(signal, sample_rate):
    """ Plot the signal in time domain """
    fig_signal = go.Figure(
        go.Scatter(x=np.arange(signal.shape[0])/sample_rate,
                   y=signal, line={'color': 'green'},
                   name='Waveform',
                   hovertemplate='Time: %{x:.2f} s<br>Amplitude: %{y:.2f}<br><extra></extra>'),
        layout={
            'height': 200,
            'xaxis': {'title': 'Time, s'},
            'yaxis': {'title': 'Amplitude'},
            'title': 'Audio Signal',
            'margin': dict(l=0, r=0, t=40, b=0, pad=0),
        }
    )
    fig_signal.show()

Output: high_score_manifest.json \\
Each line in high_score_manifest.json contains a clip path, the transcription (true label) of the clip, and the duration of the clip. In the extracting unconfident words section, we will only use the clips, and assume we do not know the real transcription

## Keywords Extraction

This section extracts a list of keywords from relevant hot text (supplemental lecture notes to the lecture). We uses YAKE package to extract the keywords. Another way to obtain potential keywords would be from places such as glossary / index of the textbook (education setting), legal terms (law setting) and etc. 

In [6]:
# read all the texts from the notes 
pdf = open(WORK_DIR + "/notes.pdf", 'rb')
pdfReader = PyPDF2.PdfFileReader(pdf)

notes_str = ""
for i in range(pdfReader.getNumPages()):
  notes_str += pdfReader.getPage(i).extractText() + " "

In [8]:
# extract keywords from the text

# parameters
relevant_threshold = 0.1 #(lower means more relevant )
max_ngram_size = 3
deduplication_threshold = 0.9
numOfKeywords = 20
extractor = yake.KeywordExtractor(top = 50)
keywords = extractor.extract_keywords(notes_str)

keyword_set = set()

for word in keywords:
  if word[1] < relevant_threshold: 
    temp_list = word[0].split()
    set_update_list = []
    for word in temp_list:
      word_split = word.split('-')
      set_update_list += word_split
      keyword_set.update(set_update_list)

In [13]:
# perform some manual update 
delete_set = set(["Note", 'Notes', 'October', 'change', 'compute', 'final', 'left', 'output', 'right', 'side'])
keyword_set.difference_update(delete_set)

In [14]:
keyword_set

{'Net',
 'Neural',
 'ascent',
 'derivative',
 'formula',
 'formulas',
 'function',
 'gradient',
 'input',
 'layer',
 'layers',
 'neuron',
 'neurons',
 'partial',
 'performance',
 'sigmoid',
 'weight',
 'weights'}

Output: keyword_set \\
A list of keywords extracted from the lecture notes. Given the context (lecture on neural net), the extracted keywords seems resonable 

## Obtaining unconfident word from each segmented audio clip

In this section, we obtain a list of unconfident words and their transcription from every clips. \\
For every clip, we: 

1.   Feed the clip through NeMo quartznet, and obtain its ctc matrix and actual transcription. 
2.   Split the clip into words based on the space prediction of the ctc matrix, and get the word level transcription by splitting based on spaces of the transcription. 
3.   Build a new clips in the format of "silence + word1 + word 2 + word 3 + word 4 + silence". This is to combat the observation that NeMo performs drastically drops when predicting individual words, to a point of non-functional. In this new format, each old clip will generate multiple new four words clips. For example, if the original clip is "Today we will discuss neural network", then the new clips are "Today we will discuss", "we will discuss neural", and "will discuss neural network". Picking the 4 words sequence is a balance between functional NeMo output and also make finding beamsearch path probabilities resonable. (Generally, longer words sequence would also means that we need larger beam width to fully explore all the possible alternatives to each word). 
4.   Feed new clips through NeMo quartznet, and obtain its ctc matrix. 
5.   Feed the ctc matrix to BeamSearch to re-discover transcript candidates 
6.   Pick all the top 1000 transcript candidates (4 words) if the highest candidate's path probability is smaller than the threshold (i.e.: Not confident about the transcription). 
7.   Split all the chosen transcript candidates into individual words, and combine them into a unique set of unconfident words. 

8.   Compare every word in the unconfident words set with every word in the key word set. If the phoentic distance (average of metaphone and dmetaphone) is higher than the threshold, add the pair into final output. (e.g.: the word "terevitive" is in the unconfident word set, and the word "derivative" is in the key word set, due to phoentic distance being close, we hypohtesized that if the model learns more about the pronunciation of two words, it will learn not to translate "derivative" as "terevitive"



In [ ]:
# get the clips as our input data, from now on we assume they are unlabeled. 
clips = []

with open(os.path.join(OUTPUT_DIR, 'manifests', high_score_manifest), 'r') as f:
  for line in f:
      sample = json.loads(line)
      #display(Audio(sample['audio_filepath']))
      #display('Reference text:       ' + sample['text_no_preprocessing'])
      #display('ASR transcript: ' + sample['transcript'])
      clips.append(sample['audio_filepath'])

In [ ]:
quartznet = nemo_asr.models.EncDecCTCModel.from_pretrained(model_name="QuartzNet15x5Base-En")

[NeMo I 2021-06-03 05:01:31 cloud:66] Downloading from: https://api.ngc.nvidia.com/v2/models/nvidia/nemospeechmodels/versions/1.0.0a5/files/QuartzNet15x5Base-En.nemo to /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo
[NeMo I 2021-06-03 05:01:38 common:675] Instantiating model from pre-trained checkpoint
[NeMo I 2021-06-03 05:01:39 features:252] PADDING: 16
[NeMo I 2021-06-03 05:01:39 features:269] STFT using torch
[NeMo I 2021-06-03 05:01:47 modelPT:434] Model EncDecCTCModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.


In [ ]:
# getting raw log probs
all_log_probs = quartznet.transcribe(paths2audio_files=clips, logprobs= True)
all_transcripts = quartznet.transcribe(paths2audio_files=clips)

[NeMo W 2021-06-03 05:02:02 patch_utils:50] torch.stft() signature has been updated for PyTorch 1.7+
    Please update PyTorch to remain compatible with later versions of NeMo.


In [ ]:

# set up necessary functions 
# splitting based on spaces, and create BeamSearch code are adopted from https://github.com/NVIDIA/NeMo/blob/main/tutorials/asr/Offline_ASR.ipynb
def softmax(logits):
    e = np.exp(logits - np.max(logits))
    return e / e.sum(axis=-1).reshape([logits.shape[0], 1])


def phoentics_cross_reference(unconfident_words, key_words, threshold):
  result_set = set()
  for word in unconfident_words:
    for kw in key_words:
      #ratio1 = fuzz.ratio(phonetics.soundex(word), phonetics.soundex(kw))
      ratio2 = fuzz.ratio(phonetics.metaphone(word), phonetics.metaphone(kw))
      ratio3 = fuzz.ratio(phonetics.dmetaphone(word), phonetics.dmetaphone(kw))
      #final_ratio = (ratio1 + ratio2 + ratio3) / 3
      final_ratio = (ratio2 + ratio3) / 2
      if final_ratio > threshold:
        result_set.update([word, kw])
  return result_set

def clip_confident_scoring(logits_output):
  probs = softmax(logits_output)

  beam_search_lm = nemo_asr.modules.BeamSearchDecoderWithLM(
      vocab=list(quartznet.decoder.vocabulary),
      beam_width=1000,
      alpha=2, beta=1.5,
      lm_path=None,
      num_cpus=max(os.cpu_count(), 1),
      input_tensor=False)  
  
  beam_result = beam_search_lm.forward(log_probs = np.expand_dims(probs, axis=0), log_probs_length=None)

  path_prob = [ele[0] for ele in beam_result[0]]

  return(np.max(path_prob), np.var(path_prob))


def get_words_candidates(clip_path, clip_transcript, clip_logprobs, keyword_set, path_threshold, phoen_dist_threshold):

  # 20ms is duration of a timestep at output of the model
  time_stride = 0.02

  # get model's alphabet
  labels = list(quartznet.decoder.vocabulary) + ['blank']
  labels[0] = 'space'

  probs = softmax(clip_logprobs)


  # get timestamps for space symbols
  spaces = []
  state = ''
  idx_state = 0

  if np.argmax(probs[0]) == 0:
      state = 'space'

  for idx in range(1, probs.shape[0]):
      current_char_idx = np.argmax(probs[idx])
      if state == 'space' and current_char_idx != 0 and current_char_idx != 28:
          spaces.append([idx_state, idx-1])
          state = ''
      if state == '':
          if current_char_idx == 0:
              state = 'space'
              idx_state = idx

  #if state == 'space':
      #spaces.append([idx_state, len(pred)-1])

  signal, sample_rate = librosa.load(clip_path, sr=None)

  # delete all temp data 
  dir = "/content/drive/MyDrive/cs230_project/MIT_usecase/TEMP"
  for files in os.listdir(dir):
      path = os.path.join(dir, files)
      try:
          shutil.rmtree(path)
      except OSError:
          os.remove(path)
  # get word level split 
  # calibration offset for timestamps: 180 ms
  offset = -0.18

  # split the transcript into words
  words = clip_transcript.split()

  # cut words
  pos_prev = 0

  # total number 
  total_4_word_clips = len(spaces)-4

  # get the 4 words combo 
  for j in range(len(spaces)-4):
      beg_spot = spaces[j]
      end_spot = spaces[j+4]
      #print(words[j], words[j+1], words[j+2], words[j+3], words[j+4])
      pos_end = offset + (end_spot[0]+end_spot[1])/2*time_stride
      #print(f"The location of the word is {int(pos_prev*sample_rate), int(pos_end*sample_rate)}")
      # concatenate silence and write to drive
      audio_w_silence = np.concatenate((np.zeros((80000,)), signal[int(pos_prev*sample_rate):int(pos_end*sample_rate)], np.zeros((80000,))))
      
      file_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TEMP/" + f"split_exp_{j}.wav"
      sf.write(file_path,audio_w_silence, sample_rate, subtype='PCM_24')
      # increment end position 
      pos_prev = offset + (beg_spot[0]+beg_spot[1])/2*time_stride

  # transcribe the word level clips
  word_level_clips = ["/content/drive/MyDrive/cs230_project/MIT_usecase/TEMP/" + f"split_exp_{j}.wav" for j in range(total_4_word_clips)]
  word_level_all_transcript = quartznet.transcribe(paths2audio_files=word_level_clips)
  word_level_all_logits = quartznet.transcribe(word_level_clips, logprobs=True)

  # get the dataframe of words, and their max prob 
  master_list = []
  for i in range(total_4_word_clips):
    temp_list = [i, word_level_all_transcript[i], clip_confident_scoring(word_level_all_logits[i])[0], clip_confident_scoring(word_level_all_logits[i])[1]]
    master_list.append(temp_list)

  master_pd = pd.DataFrame(master_list, columns = ['str_idx', 'words', 'max_prob', 'variance'])

  # get unconfident words 
  unconfident_words = set()
  for idx, row in master_pd.iterrows():
    if row['max_prob'] < path_prob_threshold:
      unconfident_words.update(row['words'].split())

  return(phoentics_cross_reference(unconfident_words, keyword_set, phoen_dist_threshold))

In [ ]:
# parameters
path_prob_threshold = -9
phoentic_sim_ratio_threshold = 90




print(f"The key word set is {keyword_set}")
print(f'The path_threshold is {path_prob_threshold}')
print(f'The phoenetic threshold is {phoentic_sim_ratio_threshold}')

The key word set is {'formulas', 'formula', 'function', 'sigmoid', 'neuron', 'weights', 'Net', 'layer', 'performance', 'input', 'ascent', 'gradient', 'derivative', 'Neural', 'layers', 'neurons', 'partial', 'weight'}
The path_threshold is -9
The phoenetic threshold is 90


In [ ]:
clip_idx = 3
clip_path = clips[clip_idx]
clip_transcript = all_transcripts[clip_idx]
clip_logprobs = all_log_probs[clip_idx]
get_words_candidates(clip_path, clip_transcript, clip_logprobs, keyword_set, path_prob_threshold, phoentic_sim_ratio_threshold)

{'Neural', 'and', 'ascent', 'input', 'neral', 'weight', 'what'}

In [ ]:
total_target_word_set = set()

for i in range(len(clips)):
  print(f'------------Processing clips {i} -------------------')
  clip_idx = i
  clip_path = clips[clip_idx]
  clip_transcript = all_transcripts[clip_idx]
  clip_logprobs = all_log_probs[clip_idx]
  word_candidate = get_words_candidates(clip_path, clip_transcript, clip_logprobs, keyword_set = keyword_set, path_threshold = path_prob_threshold, phoen_dist_threshold = phoentic_sim_ratio_threshold)
  total_target_word_set = total_target_word_set.union(word_candidate)
  print(f'The clip transcript is {clip_transcript}')
  print(f'Identified word candidate is {word_candidate}')
  print("\n")

  if i > 49:
    break 

------------Processing clips 0 -------------------



The clip transcript is to make a donation or to view additional materials from hundreds of m i t courses visit m i t open course ware at o c w
Identified word candidate is set()


------------Processing clips 1 -------------------
The clip transcript is m i t
Identified word candidate is set()


------------Processing clips 2 -------------------
The clip transcript is ete you
Identified word candidate is set()


------------Processing clips 3 -------------------



The clip transcript is well what we're going to do to day is climb a pretty big mountain because we're going to go from a neral nut with two parameters to discussing the kind of neural ness in which people end up dealing with sixty sixty million parameters
Identified word candidate is {'input', 'what', 'ascent', 'weight', 'Neural', 'and', 'neral'}


------------Processing clips 4 -------------------



The clip transcript is so tit's going to be a pretty big jump
Identified word candidate is set()


------------Processing clips 5 -------------------



The clip transcript is belongg away are a couple things i wanted to underscore from our previous discussion
Identified word candidate is {'formula', 'froma'}


------------Processing clips 6 -------------------


...


The clip transcript is so that's by way of a couple of thesides that i wanted t e underscore before we get into the um center of today's discussion which will be to talk about these so called deep nets
Identified word candidate is set()


------------Processing clips 47 -------------------



The clip transcript is now let's see what's a deep net do
Identified word candidate is set()


------------Processing clips 48 -------------------



The clip transcript is well from last time you know that a deep met does that sort of thing and it's interesting to look atto some of the uh some of the offerings here by
Identified word candidate is set()


------------Processing clips 49 -------------------



The clip transcript is how how good was this a performance in two thousand and twelve
Identified word candidate is {'performance'}


------------Processing clips 50 -------------------



The clip transcript is well turned out that the franction of the time that the system had the right answer in its top five choices was about fifteen percent
Identified word candidate is set()




In [ ]:
total_target_word_set

{'Net',
 'Neural',
 'about',
 'ado',
 'and',
 'anda',
 'aneral',
 'annural',
 'anto',
 'aperformance',
 'ascent',
 'at',
 'derivative',
 'formula',
 'from',
 'froma',
 'input',
 'it',
 'its',
 'neral',
 'net',
 'neuron',
 'neurons',
 'norin',
 'norins',
 'not',
 'note',
 'ont',
 'out',
 'partial',
 'performance',
 'performes',
 'samet',
 'scot',
 'sigmoid',
 'terevitive',
 'weight',
 'weights',
 'weightse',
 'wet',
 'what',
 'wit'}

Output: total_target_word_set \\
This is a set of words for which we will generate synthetic voices of the training dataset. 

## Generating Synthetic Voices of the Target Word Set


In this section, we generate 3 sets of trainning data based on the outputed target word above. The 3 sets of trainning data are: 


1.   Entire total target word set 
2.   One keyword and its mis-transcribed ouput ("Neural, aneral, annural, neral")
3.   One specific keyword ("Neural")

For each word, when we are generating the text to speech data, we repeated it 4 times to combat the issue of NeMo not functioning on short input. We also generate 5 perturbated data point. So each word will have 6 trainning clips. 



In [20]:
# manually create the output from previous section because running it takes a long time
total_target_word_set = {'Net','Neural','about','ado','and','anda','aneral','annural','anto','aperformance','ascent','at','derivative','formula','from','froma','input','it','its','neral','net','neuron','neurons','norin','norins','not','note','ont','out','partial','performance','performes','samet','scot','sigmoid','terevitive','weight','weights','weightse','wet','what','wit'}

In [15]:
# code copied from https://github.com/NVIDIA/NeMo/blob/main/tutorials/tts/1_TTS_inference.ipynb
from ipywidgets import Select, HBox, Label
from IPython.display import display

supported_e2e = ["fastpitch_hifigan", "fastspeech2_hifigan", None]
supported_spec_gen = ["tacotron2", "glow_tts", "talknet", "fastpitch", "fastspeech2", None]
supported_audio_gen = ["waveglow", "squeezewave", "uniglow", "melgan", "hifigan", "griffin-lim", None]

print("Select the model(s) that you want to use. Please choose either 1 end-to-end model or 1 spectrogram generator and 1 vocoder.")
e2e_selector = Select(options=supported_e2e, value=None)
spectrogram_generator_selector = Select(options=supported_spec_gen, value=None)
audio_generator_selector = Select(options=supported_audio_gen, value=None)
display(HBox([e2e_selector, Label("OR"), spectrogram_generator_selector, Label("+"), audio_generator_selector]))

Select the model(s) that you want to use. Please choose either 1 end-to-end model or 1 spectrogram generator and 1 vocoder.


In [16]:
e2e_model = e2e_selector.value
spectrogram_generator = spectrogram_generator_selector.value
audio_generator = audio_generator_selector.value

if e2e_model is None and spectrogram_generator is None and audio_generator is None:
    raise ValueError("No models were chosen. Please return to the previous step and choose either 1 end-to-end model or 1 spectrogram generator and 1 vocoder.")

if e2e_model and (spectrogram_generator or audio_generator):
    raise ValueError(
        "An end-to-end model was chosen and either a spectrogram generator or a vocoder was also selected. For end-to-end models, please select `None` "
        "in the second and third column to continue. For the two step pipeline, please select `None` in the first column to continue."
    )

if (spectrogram_generator and audio_generator is None) or (audio_generator and spectrogram_generator is None):
    raise ValueError("In order to continue with the two step pipeline, both the spectrogram generator and the audio generator must be chosen, but one was `None`")

In [ ]:
from omegaconf import OmegaConf, open_dict
import torch
from nemo.collections.tts.models.base import SpectrogramGenerator, Vocoder, TextToWaveform


def load_spectrogram_model():
    override_conf = None
    if spectrogram_generator == "tacotron2":
        from nemo.collections.tts.models import Tacotron2Model
        pretrained_model = "tts_en_tacotron2"
    elif spectrogram_generator == "glow_tts":
        from nemo.collections.tts.models import GlowTTSModel
        pretrained_model = "tts_en_glowtts"
        import wget
        from pathlib import Path
        if not Path("cmudict-0.7b").exists():
            filename = wget.download("http://svn.code.sf.net/p/cmusphinx/code/trunk/cmudict/cmudict-0.7b")
            filename = str(Path(filename).resolve())
        else:
            filename = str(Path("cmudict-0.7b").resolve())
        conf = SpectrogramGenerator.from_pretrained(pretrained_model, return_config=True)
        if "params" in conf.parser:
            conf.parser.params.cmu_dict_path = filename
        else:
            conf.parser.cmu_dict_path = filename
        override_conf = conf
    elif spectrogram_generator == "talknet":
        from nemo.collections.tts.models import TalkNetModel
        pretrained_model = "tts_en_talknet" 
    elif spectrogram_generator == "fastpitch":
        from nemo.collections.tts.models import FastPitchModel
        pretrained_model = "tts_en_fastpitch"
    elif spectrogram_generator == "fastspeech2":
        from nemo.collections.tts.models import FastSpeech2Model
        pretrained_model = "tts_en_fastspeech2"
    else:
        raise NotImplementedError

    model = SpectrogramGenerator.from_pretrained(pretrained_model, override_config_path=override_conf)
    
    if spectrogram_generator == "talknet":
        from nemo.collections.tts.models import TalkNetPitchModel
        pitch_model = TalkNetPitchModel.from_pretrained(pretrained_model, override_config_path=override_conf)
        from nemo.collections.tts.models import TalkNetDursModel
        durs_model = TalkNetDursModel.from_pretrained(pretrained_model, override_config_path=override_conf)
        model.add_module('_pitch_model', pitch_model)
        model.add_module('_durs_model', durs_model)
    
    return model


def load_vocoder_model():
    RequestPseudoInverse = False
    TwoStagesModel = False
    strict=True
    
    if audio_generator == "waveglow":
        from nemo.collections.tts.models import WaveGlowModel
        pretrained_model = "tts_waveglow"
        strict=False
    elif audio_generator == "squeezewave":
        from nemo.collections.tts.models import SqueezeWaveModel
        pretrained_model = "tts_squeezewave"
    elif audio_generator == "uniglow":
        from nemo.collections.tts.models import UniGlowModel
        pretrained_model = "tts_uniglow"
    elif audio_generator == "melgan":
        from nemo.collections.tts.models import MelGanModel
        pretrained_model = "tts_melgan"
    elif audio_generator == "hifigan":
        from nemo.collections.tts.models import HifiGanModel
        pretrained_model = "tts_hifigan"
    elif audio_generator == "griffin-lim":
        from nemo.collections.tts.models import TwoStagesModel
        cfg = {'linvocoder':  {'_target_': 'nemo.collections.tts.models.two_stages.GriffinLimModel',
                             'cfg': {'n_iters': 64, 'n_fft': 1024, 'l_hop': 256}},
               'mel2spec': {'_target_': 'nemo.collections.tts.models.two_stages.MelPsuedoInverseModel',
                           'cfg': {'sampling_rate': 22050, 'n_fft': 1024, 
                                   'mel_fmin': 0, 'mel_fmax': 8000, 'mel_freq': 80}}}
        model = TwoStagesModel(cfg)            
        TwoStagesModel = True
    else:
        raise NotImplementedError

    if not TwoStagesModel:
        model = Vocoder.from_pretrained(pretrained_model, strict=strict)
    return model

def load_e2e_model():
    if e2e_model == "fastpitch_hifigan":
        from nemo.collections.tts.models import FastPitchHifiGanE2EModel
        pretrained_model = "tts_en_e2e_fastpitchhifigan"
    elif e2e_model == "fastspeech2_hifigan":
        from nemo.collections.tts.models import FastSpeech2HifiGanE2EModel
        pretrained_model = "tts_en_e2e_fastspeech2hifigan"
    else:
        raise NotImplementedError

    model = TextToWaveform.from_pretrained(pretrained_model)
    return model

emodel = None
spec_gen = None
vocoder = None
if e2e_model:
    emodel = load_e2e_model().eval().cuda()
else:
    spec_gen = load_spectrogram_model().eval().cuda()
    vocoder = load_vocoder_model().eval().cuda()

In [18]:
def infer(emodel, spec_gen_model, vocder_model, str_input):
    parser_model = emodel or spec_gen_model
    with torch.no_grad():
        parsed = parser_model.parse(str_input)
        if emodel is None:
            spectrogram = spec_gen.generate_spectrogram(tokens=parsed)
            audio = vocoder.convert_spectrogram_to_audio(spec=spectrogram)
        else:
            spectrogram = None
            audio = emodel.convert_text_to_waveform(tokens=parsed)[0]
    if spectrogram is not None:
        if isinstance(spectrogram, torch.Tensor):
            spectrogram = spectrogram.to('cpu').numpy()
        if len(spectrogram.shape) == 3:
            spectrogram = spectrogram[0]
    if isinstance(audio, torch.Tensor):
        audio = audio.to('cpu').numpy()
    return spectrogram, audio

### Generating Training Dataset 1

In [21]:
# print out all the words that needs to be generated
print(total_target_word_set)

{'at', 'ado', 'annural', 'norin', 'weights', 'anto', 'note', 'weight', 'neuron', 'formula', 'about', 'weightse', 'terevitive', 'performance', 'derivative', 'input', 'Net', 'froma', 'out', 'from', 'aneral', 'scot', 'neurons', 'its', 'what', 'ascent', 'ont', 'and', 'performes', 'wet', 'Neural', 'wit', 'partial', 'sigmoid', 'aperformance', 'anda', 'neral', 'net', 'norins', 'samet', 'it', 'not'}


In [24]:
# speed
resample_type = 'kaiser_best'  # Can be ['kaiser_best', 'kaiser_fast', 'fft', 'scipy']
speed = perturb.SpeedPerturbation(22050, resample_type, min_speed_rate=0.5, max_speed_rate=2.0, num_rates=-1)

In [ ]:
# generate training words with pertubation 
idx = 0
file_name_to_label_dict = dict()

for word in total_target_word_set:
  # get the OG voice 
  spec, audio = infer(emodel, spec_gen, vocoder, word)

  # concate the audio with zeros and repeat it 4 times 
  audio = np.concatenate((np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,))))

  audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + f"training_exp_{idx}.wav"

  sf.write(audio_path, audio, 22050, subtype='PCM_24')
  file_name_to_label_dict[ f"training_exp_{idx}.wav"] = word

  idx += 1

  for i in range(5):
    sample_segment = segment.AudioSegment.segment_from_file(audio_path)
    speed.perturb(sample_segment)
    pertub_audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + f"training_exp_{idx}.wav"
    sf.write(pertub_audio_path, sample_segment.samples, 22050, subtype='PCM_24')
    file_name_to_label_dict[f"training_exp_{idx}.wav"] = word
    idx += 1



In [ ]:
# build manifest 
import json
train_manifest =  "/content/drive/MyDrive/cs230_project/MIT_usecase/train_manifest.json"

with open(train_manifest, 'w') as fout:
  for key, val in file_name_to_label_dict.items():
    audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + key
    duration = librosa.core.get_duration(filename=audio_path)
    transcript = val + " " + val + " " + val + " " + val 

    # Write the metadata to the manifest
    metadata = {
        "audio_filepath": audio_path,
        "duration": duration,
        "text": transcript
    }
    json.dump(metadata, fout)
    fout.write('\n')

### Generating Training Dataset 2

In [27]:
total_target_word_set = {"Neural", "aneral", "annural", "neral"}
# generate training words with pertubation 
idx = 0
file_name_to_label_dict = dict()

for word in total_target_word_set:
  # get the OG voice 
  spec, audio = infer(emodel, spec_gen, vocoder, word)

  # concate the audio with zeros and repeat it 4 times 
  audio = np.concatenate((np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,))))

  audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + f"training_exp_series2_{idx}.wav"

  sf.write(audio_path, audio, 22050, subtype='PCM_24')
  file_name_to_label_dict[ f"training_exp_series2_{idx}.wav"] = word

  idx += 1

  for i in range(5):
    sample_segment = segment.AudioSegment.segment_from_file(audio_path)
    speed.perturb(sample_segment)
    pertub_audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + f"training_exp_series2_{idx}.wav"
    sf.write(pertub_audio_path, sample_segment.samples, 22050, subtype='PCM_24')
    file_name_to_label_dict[f"training_exp_series2_{idx}.wav"] = word
    idx += 1

In [28]:
# build manifest 
import json
train_manifest =  "/content/drive/MyDrive/cs230_project/MIT_usecase/train_series2_manifest.json"

with open(train_manifest, 'w') as fout:
  for key, val in file_name_to_label_dict.items():
    audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + key
    duration = librosa.core.get_duration(filename=audio_path)
    transcript = val + " " + val + " " + val + " " + val 

    # Write the metadata to the manifest
    metadata = {
        "audio_filepath": audio_path,
        "duration": duration,
        "text": transcript
    }
    json.dump(metadata, fout)
    fout.write('\n')

### Generating Training Dataset 3

In [29]:
total_target_word_set = {"Neural"}
# generate training words with pertubation 
idx = 0
file_name_to_label_dict = dict()

for word in total_target_word_set:
  # get the OG voice 
  spec, audio = infer(emodel, spec_gen, vocoder, word)

  # concate the audio with zeros and repeat it 4 times 
  audio = np.concatenate((np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,)), audio, np.zeros((20000,))))

  audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + f"training_exp_series3_{idx}.wav"

  sf.write(audio_path, audio, 22050, subtype='PCM_24')
  file_name_to_label_dict[ f"training_exp_series3_{idx}.wav"] = word

  idx += 1

  for i in range(5):
    sample_segment = segment.AudioSegment.segment_from_file(audio_path)
    speed.perturb(sample_segment)
    pertub_audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + f"training_exp_series3_{idx}.wav"
    sf.write(pertub_audio_path, sample_segment.samples, 22050, subtype='PCM_24')
    file_name_to_label_dict[f"training_exp_series3_{idx}.wav"] = word
    idx += 1


# build manifest 
import json
train_manifest =  "/content/drive/MyDrive/cs230_project/MIT_usecase/train_series3_manifest.json"

with open(train_manifest, 'w') as fout:
  for key, val in file_name_to_label_dict.items():
    audio_path = "/content/drive/MyDrive/cs230_project/MIT_usecase/TRAINING/" + key
    duration = librosa.core.get_duration(filename=audio_path)
    transcript = val + " " + val + " " + val + " " + val 

    # Write the metadata to the manifest
    metadata = {
        "audio_filepath": audio_path,
        "duration": duration,
        "text": transcript
    }
    json.dump(metadata, fout)
    fout.write('\n')

## Generating Additional User Input

In this section, we simulate asking users to provide some additional prounciation samples and build a training data based on that. Using the word "neural net(s)" as an example, we located 10 instances of the professor speak the word "neural net(s)" from a different lecture, extracted the word, and build traning and testing data where each clip is the word repeated 4 times. 

In [ ]:
def minute_sec_mil_to_mil(min, sec, mil):
  return mil + sec * 1000 + min * 60 * 1000

In [ ]:
# load and write the transcript 
# Get the Transcript 
transcript_path = '/content/drive/MyDrive/cs230_project/MIT_usecase/MIT_AI_12A.srt'
transcript = pysrt.open(transcript_path)

sample_counter = 0
for ele in transcript:
  if "neural net" in ele.text in ele.text:
    sample_counter += 1
    print(ele.text)
    print(minute_sec_mil_to_mil(ele.start.minutes, ele.start.seconds, ele.start.milliseconds))
    print(minute_sec_mil_to_mil(ele.end.minutes, ele.end.seconds, ele.end.milliseconds))
    print("\n")
  if sample_counter == 10: break 


And we almost killed
off neural nets.
51720
54540


So it would seem
that neural nets
63870
67914


made a neural net that was
worth a darn for doing anything.
86850
90270


about neural nets,
and then they'll
98060
99334


with some neural network
he had done on recognizing
112070
116450


Jeff's neural net, by the
way, had 60 million parameters
124910
128289


There's a sample of things
that the Toronto neural net
144010
151280


And for the first time, it
demonstrated that a neural net
316225
318600


put into neural net technology,
which some say is the answer.
326150
331470


Here's what is done in
the neural net literature.
548440
551320




In [ ]:
label_dict = dict()
label_dict[0] = "neural nets"
label_dict[1] = "neural nets"
label_dict[2] = "neural net"
label_dict[3] = "neural nets"
label_dict[4] = "neural net"
label_dict[5] = "neural net"
label_dict[6] = "neural net"
label_dict[7] = "neural net"
label_dict[8] = "neural net"
label_dict[9] = "neural net"

# generate user training example 
for i in range(10):
  example_file_path = f"/content/drive/MyDrive/cs230_project/MIT_usecase/user_training/user_input_exp_{i}.wav"
  audio, sr = librosa.load(example_file_path, sr = 48000)
  audio = np.concatenate((np.zeros((40000,)), audio, np.zeros((40000,)), audio, np.zeros((40000,)), audio, np.zeros((40000,)), audio, np.zeros((40000,))))
  sample_file_path = f"/content/drive/MyDrive/cs230_project/MIT_usecase/user_training/user_input_extended_{i}.wav"
  sf.write(sample_file_path, audio, 48000, subtype='PCM_24')


# 
train_example_idx = [0, 2, 4, 5, 6]
test_example_idx = [1, 3, 7, 8, 9]



# build manifest 
import json
train_manifest =  "/content/drive/MyDrive/cs230_project/MIT_usecase/train_manifest_user.json"
test_manifest =  "/content/drive/MyDrive/cs230_project/MIT_usecase/test_manifest_user.json"

with open(train_manifest, 'w') as fout:
  for i in train_example_idx:
    audio_path = f"/content/drive/MyDrive/cs230_project/MIT_usecase/user_training/user_input_extended_{i}.wav"
    duration = librosa.core.get_duration(filename=audio_path)
    label = label_dict[i]
    transcript = label + " " + label + " " + label + " " + label 

    # Write the metadata to the manifest
    metadata = {
        "audio_filepath": audio_path,
        "duration": duration,
        "text": transcript
    }
    json.dump(metadata, fout)
    fout.write('\n')


with open(test_manifest, 'w') as fout:
  for i in test_example_idx:
    audio_path = f"/content/drive/MyDrive/cs230_project/MIT_usecase/user_training/user_input_extended_{i}.wav"
    duration = librosa.core.get_duration(filename=audio_path)
    label = label_dict[i]
    transcript = label + " " + label + " " + label + " " + label 

    # Write the metadata to the manifest
    metadata = {
        "audio_filepath": audio_path,
        "duration": duration,
        "text": transcript
    }
    json.dump(metadata, fout)
    fout.write('\n')

## NeMo Training Result Comparison 

Through out the process, we have built the following dataset: 


*   8000_MIT_AI_12B_high_score_manifest.json: This dataset contains the clips and transcripts of one entire lecture. 
*   train_manifest.json: This dataset contains synthetically genereated series of unconfident key words and their potentially mis-transcribed words. (e.g.: "Neurons" and "norin")
*   train_series2_manifest.json: This dataset contains synthetically generated keyword "neural", and its potentially mis-transcribed words. 
*   train_series3_manifest.json: This dataset contains synthetically generated keyword "neural". 
*   train_manifest_user.json: This dataset contains manually extracted additional prounciation of "neural net(s)" 
*   test_manifest_user.json: This dataset contains manually extracted additional prounciation of "neural net(s)" 




In [ ]:
!wget -P configs/ https://raw.githubusercontent.com/NVIDIA/NeMo/main/examples/asr/conf/config.yaml

In [30]:
high_score_dat_manifest = "/content/drive/MyDrive/cs230_project/MIT_usecase/output/manifests/8000_MIT_AI_12B_high_score_manifest.json"
all_target_word_manifest = "/content/drive/MyDrive/cs230_project/MIT_usecase/train_manifest.json"
one_word_w_candidate_manifest = "/content/drive/MyDrive/cs230_project/MIT_usecase/train_series2_manifest.json"
one_word_manifest = "/content/drive/MyDrive/cs230_project/MIT_usecase/train_series3_manifest.json"
user_input_train_manifest =  "/content/drive/MyDrive/cs230_project/MIT_usecase/train_manifest_user.json"
user_input_test_manifest = "/content/drive/MyDrive/cs230_project/MIT_usecase/test_manifest_user.json"

In [ ]:
pretrained = nemo_asr.models.EncDecCTCModel.from_pretrained(model_name="QuartzNet15x5Base-En")
pretrained.save_to("/content/drive/MyDrive/cs230_project/MIT_usecase/pre_training.nemo")

In [ ]:
# Base Performance 
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/pre_training.nemo" \
  --dataset  "/content/drive/MyDrive/cs230_project/MIT_usecase/output/manifests/8000_MIT_AI_12B_high_score_manifest.json"\

In [ ]:
# pre train model performance 
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/pre_training.nemo" \
  --dataset "/content/drive/MyDrive/cs230_project/MIT_usecase/test_manifest_user.json"\

### Train on user input
This section we train the model on user input of "neural net(s)" and see whether this helps the model to predict "neural net(s)" better. We know "neural net(s)" is a word that the model cannot do well based on the result from obtaining unconfident word

In [31]:
quartznet = nemo_asr.models.EncDecCTCModel.from_pretrained(model_name="QuartzNet15x5Base-En")
train_manifest =  user_input_train_manifest
test_manifest =  user_input_test_manifest

[NeMo I 2021-06-04 00:41:32 cloud:66] Downloading from: https://api.ngc.nvidia.com/v2/models/nvidia/nemospeechmodels/versions/1.0.0a5/files/QuartzNet15x5Base-En.nemo to /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo
[NeMo I 2021-06-04 00:41:47 common:675] Instantiating model from pre-trained checkpoint
[NeMo I 2021-06-04 00:41:48 features:252] PADDING: 16
[NeMo I 2021-06-04 00:41:48 features:269] STFT using torch
[NeMo I 2021-06-04 00:41:49 modelPT:434] Model EncDecCTCModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.


In [36]:
lr = 0.001
train_epochs = 10

In [37]:
# --- Config Information ---#
try:
    from ruamel.yaml import YAML
except ModuleNotFoundError:
    from ruamel_yaml import YAML
config_path = './configs/config.yaml'

yaml = YAML(typ='safe')
with open(config_path) as f:
    params = yaml.load(f)

params['model']['train_ds']['manifest_filepath'] = train_manifest
params['model']['validation_ds']['manifest_filepath'] = test_manifest
# modify the learning rate 
params['model']['optim']['lr'] = lr

# Point to the data we'll use for fine-tuning as the training set
import pytorch_lightning as pl

quartznet.setup_optimization(optim_config=params['model']['optim'])

quartznet.setup_training_data(train_data_config=params['model']['train_ds'])

# Point to the new validation data for fine-tuning
quartznet.setup_validation_data(val_data_config=params['model']['validation_ds'])

# And now we can create a PyTorch Lightning trainer and call `fit` again.
trainer = pl.Trainer(amp_level="O1",gpus=1, max_epochs=train_epochs)
trainer.fit(quartznet)

[NeMo W 2021-06-04 00:44:15 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 00:44:15 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 00:44:15 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !


[NeMo I 2021-06-04 00:44:16 collections:173] Dataset loaded with 5 files totalling 0.01 hours
[NeMo I 2021-06-04 00:44:16 collections:174] 0 files were filtered totalling 0.00 hours
[NeMo I 2021-06-04 00:44:16 collections:173] Dataset loaded with 5 files totalling 0.01 hours
[NeMo I 2021-06-04 00:44:16 collections:174] 0 files were filtered totalling 0.00 hours


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
[NeMo W 2021-06-04 00:44:17 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 00:44:17 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 00:44:17 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !

  | Name              | Type                              | Params
------------------------------------------------------------------------
0 | preprocessor      | AudioToMelSpectrogramPreprocessor | 0     
1 | encoder           | ConvASREncoder                    | 18.9 M
2 | decoder           | ConvASRDecoder                    | 29.7 K
3 | loss              | CTCLoss                           | 0     
4 | spec_augmentation | SpectrogramAugmentation           | 0     
5 | _wer              | WER                               | 0     
------------------------------------------------------------------------
18.9 M    Trainable params
0         Non-trainable params
18.9 M    Total params
75.698    Total estimated model params size (MB)


[NeMo W 2021-06-04 00:44:24 patch_utils:50] torch.stft() signature has been updated for PyTorch 1.7+
    Please update PyTorch to remain compatible with later versions of NeMo.


1

In [38]:
quartznet.save_to("/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_user.nemo")

In [ ]:
# post train model performance 
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_user.nemo" \
  --dataset "/content/drive/MyDrive/cs230_project/MIT_usecase/test_manifest_user.json"\

In [ ]:
# post train model performance on overall lecture dataset  
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_user.nemo" \
  --dataset  "/content/drive/MyDrive/cs230_project/MIT_usecase/output/manifests/8000_MIT_AI_12B_high_score_manifest.json"\

### Train on synthetic input "neural"

In [82]:
quartznet = nemo_asr.models.EncDecCTCModel.from_pretrained(model_name="QuartzNet15x5Base-En")
train_manifest =  one_word_manifest
test_manifest =  user_input_test_manifest

[NeMo I 2021-06-04 02:06:24 cloud:56] Found existing object /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.
[NeMo I 2021-06-04 02:06:24 cloud:62] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo
[NeMo I 2021-06-04 02:06:24 common:675] Instantiating model from pre-trained checkpoint
[NeMo I 2021-06-04 02:06:25 features:252] PADDING: 16
[NeMo I 2021-06-04 02:06:25 features:269] STFT using torch
[NeMo I 2021-06-04 02:06:26 modelPT:434] Model EncDecCTCModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.


In [83]:
lr = 0.001
train_epochs = 500

In [84]:
# --- Config Information ---#
try:
    from ruamel.yaml import YAML
except ModuleNotFoundError:
    from ruamel_yaml import YAML
config_path = './configs/config.yaml'

yaml = YAML(typ='safe')
with open(config_path) as f:
    params = yaml.load(f)

params['model']['train_ds']['manifest_filepath'] = train_manifest
params['model']['validation_ds']['manifest_filepath'] = test_manifest
# modify the learning rate 
params['model']['optim']['lr'] = lr

# Point to the data we'll use for fine-tuning as the training set
import pytorch_lightning as pl

quartznet.setup_optimization(optim_config=params['model']['optim'])

quartznet.setup_training_data(train_data_config=params['model']['train_ds'])

# Point to the new validation data for fine-tuning
quartznet.setup_validation_data(val_data_config=params['model']['validation_ds'])

# And now we can create a PyTorch Lightning trainer and call `fit` again.
trainer = pl.Trainer(amp_level="O1",gpus=1, max_epochs=train_epochs)
trainer.fit(quartznet)

[NeMo W 2021-06-04 02:06:31 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 02:06:31 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 02:06:31 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !


[NeMo I 2021-06-04 02:06:31 collections:173] Dataset loaded with 6 files totalling 0.01 hours
[NeMo I 2021-06-04 02:06:31 collections:174] 0 files were filtered totalling 0.00 hours
[NeMo I 2021-06-04 02:06:31 collections:173] Dataset loaded with 5 files totalling 0.01 hours
[NeMo I 2021-06-04 02:06:31 collections:174] 0 files were filtered totalling 0.00 hours


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
[NeMo W 2021-06-04 02:06:31 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 02:06:31 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 02:06:31 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !

  | Name              | Type                              | Params
------------------------------------------------------------------------
0 | preprocessor      | AudioToMelSpectrogramPreprocessor | 0     
1 | encoder           | ConvASREncoder                    | 18.9 M
2 | decoder           | ConvASRDecoder                    | 29.7 K
3 | loss              | CTCLoss                           | 0     
4 | spec_augmentation | SpectrogramAugmentation           | 0     
5 | _wer              | WER                               | 0     
------------------------------------------------------------------------
18.9 M    Trainable params
0         Non-trainable params
18.9 M    Total params
75.698    Total estimated model params size (MB)


1

In [90]:
quartznet.save_to("/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_series3.nemo")

In [89]:
quartznet.transcribe(paths2audio_files = ["/content/drive/MyDrive/cs230_project/MIT_usecase/user_training/user_input_extended_5.wav"])

['euralal euralal euralal euralal']

In [91]:
# post train model performance 
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_series3.nemo" \
  --dataset "/content/drive/MyDrive/cs230_project/MIT_usecase/test_manifest_user.json"\

[NeMo W 2021-06-04 02:29:36 optimizers:46] Apex was not found. Using the lamb optimizer will error out.
2021-06-04 02:29:37.376864: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
################################################################################
### WARNING, path does not exist: KALDI_ROOT=/mnt/matylda5/iveselyk/Tools/kaldi-trunk
###          (please add 'export KALDI_ROOT=<your_path>' in your $HOME/.profile)
###          (or run as: KALDI_ROOT=<your_path> python <your_script>.py)
################################################################################

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package cmudict to /root/nltk_data...
[nltk_data]   Package cmudict is already up-to-date!
[NeMo W 2021-06-04 02:29:40 experimental:28]

In [ ]:
# post train model performance on overall lecture dataset  
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_user.nemo" \
  --dataset  "/content/drive/MyDrive/cs230_project/MIT_usecase/output/manifests/8000_MIT_AI_12B_high_score_manifest.json"\

### Train on synthetic input of "neural" and its candidates

In [93]:
quartznet = nemo_asr.models.EncDecCTCModel.from_pretrained(model_name="QuartzNet15x5Base-En")
train_manifest =  one_word_w_candidate_manifest
test_manifest =  user_input_test_manifest

[NeMo I 2021-06-04 02:34:40 cloud:56] Found existing object /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.
[NeMo I 2021-06-04 02:34:40 cloud:62] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo
[NeMo I 2021-06-04 02:34:40 common:675] Instantiating model from pre-trained checkpoint
[NeMo I 2021-06-04 02:34:41 features:252] PADDING: 16
[NeMo I 2021-06-04 02:34:41 features:269] STFT using torch
[NeMo I 2021-06-04 02:34:42 modelPT:434] Model EncDecCTCModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.


In [95]:
lr = 0.001
train_epochs = 100

In [96]:
# --- Config Information ---#
try:
    from ruamel.yaml import YAML
except ModuleNotFoundError:
    from ruamel_yaml import YAML
config_path = './configs/config.yaml'

yaml = YAML(typ='safe')
with open(config_path) as f:
    params = yaml.load(f)

params['model']['train_ds']['manifest_filepath'] = train_manifest
params['model']['validation_ds']['manifest_filepath'] = test_manifest
# modify the learning rate 
params['model']['optim']['lr'] = lr

# Point to the data we'll use for fine-tuning as the training set
import pytorch_lightning as pl

quartznet.setup_optimization(optim_config=params['model']['optim'])

quartznet.setup_training_data(train_data_config=params['model']['train_ds'])

# Point to the new validation data for fine-tuning
quartznet.setup_validation_data(val_data_config=params['model']['validation_ds'])

# And now we can create a PyTorch Lightning trainer and call `fit` again.
trainer = pl.Trainer(amp_level="O1",gpus=1, max_epochs=train_epochs)
trainer.fit(quartznet)

[NeMo W 2021-06-04 02:34:59 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 02:34:59 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 02:34:59 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !


[NeMo I 2021-06-04 02:34:59 collections:173] Dataset loaded with 24 files totalling 0.06 hours
[NeMo I 2021-06-04 02:34:59 collections:174] 0 files were filtered totalling 0.00 hours
[NeMo I 2021-06-04 02:34:59 collections:173] Dataset loaded with 5 files totalling 0.01 hours
[NeMo I 2021-06-04 02:34:59 collections:174] 0 files were filtered totalling 0.00 hours


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
[NeMo W 2021-06-04 02:34:59 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 02:34:59 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 02:35:00 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !

  | Name              | Type                              | Params
------------------------------------------------------------------------
0 | preprocessor      | AudioToMelSpectrogramPreprocessor | 0     
1 | encoder           | ConvASREncoder                    | 18.9 M
2 | decoder           | ConvASRDecoder                    | 29.7 K
3 | loss              | CTCLoss                           | 0     
4 | spec_augmentation | SpectrogramAugmentation           | 0     
5 | _wer              | WER                               | 0     
------------------------------------------------------------------------
18.9 M    Trainable params
0         Non-trainable params
18.9 M    Total params
75.698    Total estimated model params size (MB)


1

In [98]:
quartznet.save_to("/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_series2.nemo")

In [99]:
# post train model performance 
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_series2.nemo" \
  --dataset "/content/drive/MyDrive/cs230_project/MIT_usecase/test_manifest_user.json"\

[NeMo W 2021-06-04 02:45:57 optimizers:46] Apex was not found. Using the lamb optimizer will error out.
2021-06-04 02:45:58.799826: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
################################################################################
### WARNING, path does not exist: KALDI_ROOT=/mnt/matylda5/iveselyk/Tools/kaldi-trunk
###          (please add 'export KALDI_ROOT=<your_path>' in your $HOME/.profile)
###          (or run as: KALDI_ROOT=<your_path> python <your_script>.py)
################################################################################

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package cmudict to /root/nltk_data...
[nltk_data]   Package cmudict is already up-to-date!
[NeMo W 2021-06-04 02:46:01 experimental:28]

### Train on synthetic input of entire difficult word set

In [114]:
quartznet = nemo_asr.models.EncDecCTCModel.from_pretrained(model_name="QuartzNet15x5Base-En")
train_manifest =  all_target_word_manifest
test_manifest =  high_score_dat_manifest

[NeMo I 2021-06-04 04:47:08 cloud:56] Found existing object /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.
[NeMo I 2021-06-04 04:47:08 cloud:62] Re-using file from: /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo
[NeMo I 2021-06-04 04:47:08 common:675] Instantiating model from pre-trained checkpoint
[NeMo I 2021-06-04 04:47:09 features:252] PADDING: 16
[NeMo I 2021-06-04 04:47:09 features:269] STFT using torch
[NeMo I 2021-06-04 04:47:09 modelPT:434] Model EncDecCTCModel was successfully restored from /root/.cache/torch/NeMo/NeMo_1.0.0/QuartzNet15x5Base-En/2b066be39e9294d7100fb176ec817722/QuartzNet15x5Base-En.nemo.


In [115]:
lr = 0.001
train_epochs = 5

In [116]:
# --- Config Information ---#
try:
    from ruamel.yaml import YAML
except ModuleNotFoundError:
    from ruamel_yaml import YAML
config_path = './configs/config.yaml'

yaml = YAML(typ='safe')
with open(config_path) as f:
    params = yaml.load(f)

params['model']['train_ds']['manifest_filepath'] = train_manifest
params['model']['validation_ds']['manifest_filepath'] = test_manifest
# modify the learning rate 
params['model']['optim']['lr'] = lr

# Point to the data we'll use for fine-tuning as the training set
import pytorch_lightning as pl

quartznet.setup_optimization(optim_config=params['model']['optim'])

quartznet.setup_training_data(train_data_config=params['model']['train_ds'])

# Point to the new validation data for fine-tuning
quartznet.setup_validation_data(val_data_config=params['model']['validation_ds'])

# And now we can create a PyTorch Lightning trainer and call `fit` again.
trainer = pl.Trainer(amp_level="O1",gpus=1, max_epochs=train_epochs)
trainer.fit(quartznet)

[NeMo W 2021-06-04 04:47:16 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 04:47:16 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 04:47:16 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !


[NeMo I 2021-06-04 04:47:16 collections:173] Dataset loaded with 252 files totalling 0.58 hours
[NeMo I 2021-06-04 04:47:16 collections:174] 0 files were filtered totalling 0.00 hours
[NeMo I 2021-06-04 04:47:16 collections:173] Dataset loaded with 435 files totalling 0.65 hours
[NeMo I 2021-06-04 04:47:16 collections:174] 0 files were filtered totalling 0.00 hours


GPU available: True, used: True
TPU available: False, using: 0 TPU cores
LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]
[NeMo W 2021-06-04 04:47:17 modelPT:640] Trainer wasn't specified in model constructor. Make sure that you really wanted it.


[NeMo I 2021-06-04 04:47:17 modelPT:748] Optimizer config = Novograd (
    Parameter Group 0
        amsgrad: False
        betas: [0.8, 0.5]
        eps: 1e-08
        grad_averaging: False
        lr: 0.001
        weight_decay: 0.001
    )


[NeMo W 2021-06-04 04:47:17 lr_scheduler:601] Neither `max_steps` nor `iters_per_batch` were provided to `optim.sched`, cannot compute effective `max_steps` !
    Scheduler will not be instantiated !

  | Name              | Type                              | Params
------------------------------------------------------------------------
0 | preprocessor      | AudioToMelSpectrogramPreprocessor | 0     
1 | encoder           | ConvASREncoder                    | 18.9 M
2 | decoder           | ConvASRDecoder                    | 29.7 K
3 | loss              | CTCLoss                           | 0     
4 | spec_augmentation | SpectrogramAugmentation           | 0     
5 | _wer              | WER                               | 0     
------------------------------------------------------------------------
18.9 M    Trainable params
0         Non-trainable params
18.9 M    Total params
75.698    Total estimated model params size (MB)


1

In [117]:
quartznet.save_to("/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_series1.nemo")

In [118]:
# post train model performance 
!python /content/NeMo/examples/asr/speech_to_text_infer.py \
  --asr_model "/content/drive/MyDrive/cs230_project/MIT_usecase/post_training_series1.nemo" \
  --dataset "/content/drive/MyDrive/cs230_project/MIT_usecase/output/manifests/8000_MIT_AI_12B_high_score_manifest.json"\

[NeMo W 2021-06-04 04:53:02 optimizers:46] Apex was not found. Using the lamb optimizer will error out.
2021-06-04 04:53:03.639793: I tensorflow/stream_executor/platform/default/dso_loader.cc:53] Successfully opened dynamic library libcudart.so.11.0
################################################################################
### WARNING, path does not exist: KALDI_ROOT=/mnt/matylda5/iveselyk/Tools/kaldi-trunk
###          (please add 'export KALDI_ROOT=<your_path>' in your $HOME/.profile)
###          (or run as: KALDI_ROOT=<your_path> python <your_script>.py)
################################################################################

[nltk_data] Downloading package averaged_perceptron_tagger to
[nltk_data]     /root/nltk_data...
[nltk_data]   Package averaged_perceptron_tagger is already up-to-
[nltk_data]       date!
[nltk_data] Downloading package cmudict to /root/nltk_data...
[nltk_data]   Package cmudict is already up-to-date!
[NeMo W 2021-06-04 04:53:06 experimental:28]

### Results

Result: \

Base Performance\
 > On lecture dataset: 0.2 \
 > On keyword: 0.95


 on lecture dataset: 0.2 \

Train on user Input \

> lr = 0.001, epochs = 10 \
>> post-trained performance: 0.45 \
>> post-trained performance on lecture dataset: 0.26\


Train on synthetic generated key word \

> lr = 0.001, epochs = 10
>> post-trained performance: 1 \

> lr = 0.001, epochs = 20
>> post-trained performance: 1 \

> lr = 0.001, epochs = 50
>> post-trained performance: 1 \

> lr = 0.001, epochs = 100
>> post-trained performance: 1 \

> lr = 0.001, epochs = 500
>> post-trained performance: 1 \
>> post-trained performance on lecture dataset: 0.26\


Train on synthetic generated key word and its candidates \
> lr = 0.001, epochs = 100
>> post-trained performance: 1 \


Train on synthetic generated all key word and its candidates \
> lr = 0.001, epochs = 100
>> post-trained performance on lecture dataset: 0.75 \

> lr = 0.001, epochs = 10
>> post-trained performance on lecture dataset: 0.75 \

> lr = 0.001, epochs = 5
>> post-trained performance on lecture dataset: 0.57 \

> lr = 0.0001, epochs = 5
>> post-trained performance on lecture dataset: 0.74 \

## Code Cited 

* https://colab.research.google.com/github/NVIDIA/NeMo/blob/main/tutorials/tools/CTC_Segmentation_Tutorial.ipynb
* https://github.com/NVIDIA/NeMo/blob/main/tutorials/asr/Offline_ASR.ipynb
* https://github.com/NVIDIA/NeMo/blob/main/tutorials/tts/1_TTS_inference.ipynb



